In [1]:
import pandas as pd
from IPython.display import clear_output, Markdown, Math
import ipywidgets as widgets
import os
import glob
import json
import numpy as np
import itertools
import sklearn.utils as sku
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer, HashingVectorizer
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import MultiLabelBinarizer
import nltk
from keras.models import load_model
from sklearn.externals import joblib
import pickle
import operator
from sklearn.pipeline import Pipeline
nltk.download('punkt')
nltk.download('averaged_perceptron_tagger')
nltk.download('wordnet')

/home/jonas/.local/lib/python3.6/site-packages/h5py/__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters
Using TensorFlow backend.


[nltk_data] Downloading package punkt to /home/jonas/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /home/jonas/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!
[nltk_data] Downloading package wordnet to /home/jonas/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


True

In [2]:
import sys
sys.path.append("..")

from Tools.Emoji_Distance import sentiment_vector_to_emoji
from Tools.Emoji_Distance import emoji_to_sentiment_vector

def emoji2sent(emoji_arr, only_emoticons=True):
    return np.array([emoji_to_sentiment_vector(e, only_emoticons=only_emoticons) for e in emoji_arr])

def sent2emoji(sent_arr, custom_target_emojis=None, only_emoticons=True):
    return [sentiment_vector_to_emoji(s, custom_target_emojis=custom_target_emojis, only_emoticons=only_emoticons) for s in sent_arr]

In [3]:
SINGLE_LABEL = True

----
## classes and functions we are using later:
----

* functions for selecting items from a set / list

In [4]:
def latest(lst):
    return lst[-1] if len(lst) > 0 else 'X' 
def most_common(lst):
    # trying to find the most common used emoji in the given lst
    return max(set(lst), key=lst.count) if len(lst) > 0 else "X" # setting label to 'X' if there is an empty emoji list

* our emoji blacklist (skin and sex modifiers)

In [5]:
# defining blacklist for modifier emojis:
emoji_blacklist = set([
    chr(0x1F3FB),
    chr(0x1F3FC),
    chr(0x1F3FD),
    chr(0x1F3FE),
    chr(0x1F3FF),
    chr(0x2642),
    chr(0x2640)
])

* lemmatization helper functions

In [6]:
from nltk.stem.snowball import SnowballStemmer
from nltk.stem import WordNetLemmatizer
from nltk import pos_tag
from nltk import word_tokenize
from nltk.corpus import wordnet

def get_wordnet_pos(treebank_tag):

    if treebank_tag.startswith('J'):
        return wordnet.ADJ
    elif treebank_tag.startswith('V'):
        return wordnet.VERB
    elif treebank_tag.startswith('N'):
        return wordnet.NOUN
    elif treebank_tag.startswith('R'):
        return wordnet.ADV
    else:
        return wordnet.NOUN

* the sample data manager loads and preprocesses data

In [11]:
class sample_data_manager(object):
    @staticmethod
    def generate_and_read(path:str, only_emoticons=True, apply_stemming=True, n_top_emojis=-1, file_range=None):
        sdm = sample_data_manager(path)
        sdm.read_files(file_index_range=range(sdm.n_files) if file_range is None else file_range, only_emoticons=only_emoticons)
        if apply_stemming:
            sdm.apply_stemming_and_lemmatization()
        
        sdm.generate_emoji_count_and_weights()
        
        if n_top_emojis > 0:
            sdm.filter_by_top_emojis(n_top=n_top_emojis)
        
        return sdm
        
    
    def __init__(self, data_root_folder:str):
        self.data_root_folder = data_root_folder
        self.json_files = sorted(glob.glob(self.data_root_folder + "/*.json"))
        self.n_files = len(self.json_files)
        self.raw_data = None
        self.emojis = None
        self.plain_text = None
        self.labels = None
        self.emoji_count = None
        self.emoji_weights = None
        self.X = None
        self.y = None
        self.Xt = None
        self.yt = None
        self.top_emojis = None
    
    def read_files(self, file_index_range:list, only_emoticons=True):
        assert np.min(file_index_range) >= 0 and np.max(file_index_range) < self.n_files
        for i in file_index_range:
            print("reading file: " + self.json_files[i] + "...")
            if self.raw_data is None:
                self.raw_data = pd.read_json(self.json_files[i], encoding="utf-8")
            else:
                self.raw_data = self.raw_data.append(pd.read_json(self.json_files[i], encoding="utf-8"))
        
        self.emojis = self.raw_data['EMOJI']
        self.plain_text = self.raw_data['text']
        
        # replacing keywords. TODO: maybe these information can be extracted and used
        self.plain_text = self.plain_text.str.replace("(<EMOJI>|<USER>|<HASHTAG>)","").str.replace("[" + "".join(list(emoji_blacklist)) + "]","")
        
        # so far filtering for the latest emoji. TODO: maybe there are also better approaches
        self.labels = emoji2sent([latest(e) for e in self.emojis], only_emoticons=only_emoticons )
        
        # and filter out all samples we have no label for:
        wrong_labels = np.isnan(np.linalg.norm(self.labels, axis=1))    

        self.labels = self.labels[np.invert(wrong_labels)]
        self.plain_text = self.plain_text[np.invert(wrong_labels)]
        self.emojis = self.emojis[np.invert(wrong_labels)]
        
        print("imported " + str(len(self.labels)) + " samples")
    
    def apply_stemming_and_lemmatization(self):
        stemmer = SnowballStemmer("english")
        for key in self.plain_text.keys():
            stemmed_sent = []
            for word in self.plain_text[key].split(" "):
                word_stemmed = stemmer.stem(word)
                stemmed_sent.append(word_stemmed)
            stemmed_sent = (" ").join(stemmed_sent)
            self.plain_text[key] = stemmed_sent
            
        lemmatizer = WordNetLemmatizer()
        for key in self.plain_text.keys():
            lemmatized_sent = []
            sent_pos = pos_tag(word_tokenize(self.plain_text[key]))
            for word in sent_pos:
                wordnet_pos = get_wordnet_pos(word[1].lower())
                word_lemmatized = lemmatizer.lemmatize(word[0], pos=wordnet_pos)
                lemmatized_sent.append(word_lemmatized)
            lemmatized_sent = (" ").join(lemmatized_sent)
            self.plain_text[key] = lemmatized_sent
    
    def generate_emoji_count_and_weights(self):
        self.emoji_count = {}
        for e_list in self.emojis:
            for e in set(e_list):
                if e not in self.emoji_count:
                    self.emoji_count[e] = 0
                self.emoji_count[e] += 1
        
        emoji_sum = sum([self.emoji_count[e] for e in self.emoji_count])

        self.emoji_weights = {}
        for e in self.emoji_count:
            # tfidf for emojis
            self.emoji_weights[e] = np.log((emoji_sum / self.emoji_count[e]))

        weights_sum= sum([self.emoji_weights[x] for x in self.emoji_weights])

        # normalize:
        for e in self.emoji_weights:
            self.emoji_weights[e] = self.emoji_weights[e] / weights_sum

        self.emoji_weights['X'] = 0  # dummy values
        self.emoji_count['X'] = 0
    
    def get_emoji_count(self):
        sorted_emoji_count = list(reversed(sorted(self.emoji_count.items(), key=operator.itemgetter(1))))
        #display(sorted_emoji_count)
        return sorted_emoji_count
    
    def filter_by_top_emojis(self,n_top = 20):
        self.top_emojis = [x[0] for x in self.get_emoji_count()[:n_top]]
        in_top = [sentiment_vector_to_emoji(x) in self.top_emojis for x in self.labels]
        self.labels = self.labels[in_top]
        self.plain_text = self.plain_text[in_top]
        self.emojis = self.emojis[in_top]
        print("remaining samples after top emoji filtering: ", len(self.labels))
    
    def create_train_test_split(self, split = 0.1, random_state = 4222):
        self.X, self.Xt, self.y, self.yt = train_test_split(self.plain_text, self.labels, test_size=split, random_state=random_state)



* the pipeline manager saves and stores sklearn pipelines. Keras models are handled differently, so the have to be named explicitly during save and load operations

In [21]:
class pipeline_manager(object):
    @staticmethod
    def load_pipeline_from_files(file_prefix:str, keras_models = [], all_models = []):
        pm = pipeline_manager(keras_models=keras_models)
        pm.load(file_prefix, all_models)
        return pm
    
    @staticmethod
    def create_keras_pipeline_with_vectorizer(vectorizer, layers, sdm:sample_data_manager):
        '''
        creates pipeline with vectorizer and keras classifier
        '''
        from keras.models import Sequential
        from keras.layers import Dense
        
        if sdm.X is None:
            sdm.create_train_test_split()
        
        vec_train = vectorizer.fit_transform(sdm.X)
        vec_test = vectorizer.transform(sdm.Xt)
        # creating keras model:
        model=Sequential()
        
        keras_layers = []
        first_layer = True
        for layer in layers:
            if first_layer:
                model.add(Dense(units=layer[0], activation=layer[1], input_dim=vectorizer.transform([" "])[0]._shape[1]))
                first_layer = False
            else:
                model.add(Dense(units=layer[0], activation=layer[1]))
        
        model.compile(loss='mean_squared_error',
                  optimizer='adam')
        
        pipeline = Pipeline([
            ('vectorizer',vectorizer),
            ('keras_model', model)
        ])
        
        return pipeline_manager(pipeline=pipeline, keras_models=['keras_model'])
    
    @staticmethod
    def create_pipeline_with_classifier_and_vectorizer(vectorizer, classifier, sdm:sample_data_manager = None):
        '''
        creates a pipeline with vectorizer and classifier for non keras classifiers
        if sample data manager is given, the vectorizer will be also fitted!
        '''
        if sdm is not None:
            if sdm.X is None:
                sdm.create_train_test_split()

            vec_train = vectorizer.fit_transform(sdm.X)
            vec_test = vectorizer.transform(sdm.Xt)
        
        pipeline = Pipeline([
            ('vectorizer',vectorizer),
            ('classifier', classifier)
        ])
        
        return pipeline_manager(pipeline=pipeline, keras_models=[])
    
    def __init__(self, pipeline = None, keras_models = []):
        self.pipeline = pipeline
        self.additional_objects = {}
        self.keras_models = keras_models
    
    def save(self, prefix:str):
        print(self.keras_models)
        # doing this like explained here: https://stackoverflow.com/a/43415459
        for step in self.pipeline.named_steps:
            if step in self.keras_models:
                self.pipeline.named_steps[step].model.save(prefix + "." + step)
            else:
                joblib.dump(self.pipeline.named_steps[step], prefix + "." + str(step))
        
        load_command = "pipeline_manager.load_pipeline_from_files( '"
        load_command += prefix + "', " + str(self.keras_models) + ", "
        load_command += str(list(self.pipeline.named_steps.keys())) + ")"
        
        import __main__ as main
        if not hasattr(main, '__file__'):
            display("saved pipeline. It can be loaded the following way:")
            display(Markdown("> ```\n"+load_command+"\n```"))
        else:
            print("saved pipeline. It can be loaded the following way:")
            print(load_command)
        
    
    def load(self, prefix:str, models = []):
        self.pipeline = None
        model_list = []
        for model in models:
            if model in self.keras_models:
                model_list.append((model, load_model(prefix + "." + model)))
            else:
                model_list.append((model, joblib.load(prefix+"." + model)))
        self.pipeline = Pipeline(model_list)
    
    def fit(self,X,y):
        self.pipeline.fit(X,y)
    
    def predict(self,X):
        return self.pipeline.predict(X)
    

* the trainer class passes Data from the sample manager to the pipeline manager

In [9]:
class trainer(object):
    def __init__(self, sdm:sample_data_manager, pm:pipeline_manager):
        self.sdm = sdm
        self.pm = pm
    
    def fit(self, max_size=10000, disabled_fit_steps=['vectorizer']):
        # TODO: make batch fitting available here (eg: continous waiting for data and fitting them)
        if self.sdm.X is None:
            self.sdm.create_train_test_split()
        disabled_fits = {}
        disabled_fit_transforms = {}
        
        named_steps = self.pm.pipeline.named_steps
        
        for s in disabled_fit_steps:
            # now it gets a little bit dirty:
            # replace fit functions we don't want to call again (e.g. for vectorizers)
            disabled_fits[s] = named_steps[s].fit
            disabled_fit_transforms[s] = named_steps[s].fit_transform
            named_steps[s].fit = lambda self, X, y=None: self
            named_steps[s].fit_transform = named_steps[s].transform
            
        self.pm.fit(X = self.sdm.X[:max_size], y = self.sdm.y[:max_size])
        
        # restore replaced fit functions:
        for s in disabled_fit_steps:
            named_steps[s].fit = disabled_fits[s]
            named_steps[s].fit_transform = disabled_fit_transforms[s]
    
    def test(self):
        '''
        return: prediction:list, teacher:list
        '''
        if self.sdm.X is None:
            self.sdm.create_train_test_split()
        return self.pm.predict(self.sdm.Xt), self.sdm.yt

    

----
## Train

* when in notebook environment: run the stuff below:

In [12]:
import __main__ as main
if not hasattr(main, '__file__'):
    # we are in an interactive environment (probably in jupyter)
    # load data:
    sdm = sample_data_manager.generate_and_read(path="./data_en/", n_top_emojis=20, file_range=range(1))
    

reading file: ./data_en/2017-11-01.json...
imported 33368 samples
remaining samples after top emoji filtering:  26197


In [22]:
    #pm = pipeline_manager.create_keras_pipeline_with_vectorizer(vectorizer=TfidfVectorizer(stop_words='english'),
    #                                                           layers=[(10000, 'relu'),(5000, 'relu'),(2500, 'relu'),(y1[0].shape[0],None)], sdm=sdm)
    pm = pipeline_manager.create_keras_pipeline_with_vectorizer(vectorizer=TfidfVectorizer(stop_words='english'),
                                                           layers=[(2500, 'relu'),(3,None)], sdm=sdm)
    
    tr = trainer(sdm=sdm, pm=pm)
    tr.fit(100)

Epoch 1/1
100/100 [==============================] - 3s 27ms/step - loss: 0.1225


----
## save classifier

In [23]:
pm.save('custom_classifier')

['keras_model']


'saved pipeline. It can be loaded the following way:'

> ```
pipeline_manager.load_pipeline_from_files( 'custom_classifier', ['keras_model'], ['vectorizer', 'keras_model'])
```

----
## Prediction

In [33]:
import __main__ as main
if not hasattr(main, '__file__'):
    pred, teacher = tr.test()
    
    display(pred)
    display(teacher)
    
    print('prediction variance: ', np.linalg.norm(np.var(pred, axis=0)))
    print('teacher variance: ', np.linalg.norm(np.var(teacher, axis=0)))
    
    # build a dataframe to visualize test results:
    testlist = pd.DataFrame({'text': sdm.Xt, 
                         'teacher': sent2emoji(sdm.yt),
                         'teacher_sentiment': sdm.yt.tolist(),
                         'predict': sent2emoji(pred, custom_target_emojis=sdm.top_emojis),
                         'predicted_sentiment': pred.tolist()})
    # display:
    display(testlist.head())
    
    # mean squared error:
    teacher_sentiments = np.array([sample[1]['teacher_sentiment'] for sample in testlist.iterrows()])
    predicted_sentiments = np.array([sample[1]['predicted_sentiment'] for sample in testlist.iterrows()])

    mean_squared_error = ((teacher_sentiments - predicted_sentiments)**2).mean(axis=0)
    print("Mean Squared Error: ", mean_squared_error)
    print("Variance teacher: ", np.var(teacher_sentiments, axis=0))
    print("Variance prediction: ", np.var(predicted_sentiments, axis=0))
    
    # save to csv:
    testlist.to_csv('test.csv')

array([[0.15801723, 0.11859037, 0.10975348],
       [0.17035495, 0.10913695, 0.09354854],
       [0.11777218, 0.06569621, 0.06620223],
       ...,
       [0.14746301, 0.09480572, 0.08052498],
       [0.15932804, 0.11895895, 0.10343507],
       [0.17135939, 0.1061406 , 0.09402546]], dtype=float32)

array([[0.46813021, 0.24716181, 0.28470797],
       [0.46813021, 0.24716181, 0.28470797],
       [0.70401758, 0.05932203, 0.23666039],
       ...,
       [0.46813021, 0.24716181, 0.28470797],
       [0.46813021, 0.24716181, 0.28470797],
       [0.46813021, 0.24716181, 0.28470797]])

prediction variance:  0.0006294687
teacher variance:  0.03341702104519965


predict                                predicted_sentiment teacher  \
35671       😢  [0.15801723301410675, 0.11859036982059479, 0.1...       😂   
25683       😢  [0.1703549474477768, 0.10913695394992828, 0.09...       😂   
8985        😢  [0.1177721843123436, 0.06569620966911316, 0.06...       😊   
5410        😢  [0.18182337284088135, 0.12382747232913971, 0.0...       😂   
62611       😢  [0.1786666363477707, 0.11502400785684586, 0.10...       😊   

                                       teacher_sentiment  \
35671  [0.46813021474490496, 0.24716181096977158, 0.2...   
25683  [0.46813021474490496, 0.24716181096977158, 0.2...   
8985   [0.7040175768989329, 0.059322033898305086, 0.2...   
5410   [0.46813021474490496, 0.24716181096977158, 0.2...   
62611  [0.7040175768989329, 0.059322033898305086, 0.2...   

                                                    text  
35671    i feel like i care so much more in everi situat  
25683  i did not meat to add that 2 there ... hav see...  
8985                                              never…  
5410            lmao on me ! ! ! wtf wa he suppos to say  
62611  this dude alway help me get through my school ...

Mean Squared Error:  [0.14140389 0.04240099 0.02944344]
Variance teacher:  [0.02183094 0.02513847 0.00285735]
Variance prediction:  [0.00053908 0.00024232 0.00021658]


----
## Load classifier

In [ ]:
import __main__ as main
if not hasattr(main, '__file__'):
    try:
        pm
    except NameError:
        pass
    else:
        del pm # delete existing pipeline manager if ther is one

    pm = pipeline_manager.load_pipeline_from_files( 'custom_classifier', ['keras_model'], ['vectorizer', 'keras_model'])
    lookup_emojis = [#'😂',
         '😭',
         '😍',
         '😩',
         '😊',
         '😘',
         '🙏',
         '🙌',
         '😉',
         '😁',
         '😅',
         '😎',
         '😢',
         '😒',
         '😏',
         '😌',
         '😔',
         '😋',
         '😀',
         '😤']
    out = widgets.Output()

    t = widgets.Text()
    b = widgets.Button(
        description='get emoji',
        disabled=False,
        button_style='', # 'success', 'info', 'warning', 'danger' or ''
        tooltip='Click me',
        icon='check'
    )



    def handle_submit(sender):
        with out:
            clear_output()
        with out:
            pred = pm.predict([t.value])

            display(Markdown("# Predicted Emoji " + str(sent2emoji(pred, lookup_emojis)[0])))
            display(Markdown("# Sentiment Vector: $$ \pmatrix{" + str(pred[0,0]) +
                             "\\\\" + str(pred[0,1]) + "\\\\" + str(pred[0,2]) + "}$$"))

    b.on_click(handle_submit)

    display(t)
    display(widgets.VBox([b, out]))  

# simple twitter approach
*for learning emoji usage by single (in the meaning of unconnected) twitter messages*

## loading train data

* Download preprocessed raw data:
    * [here](https://the-cake-is-a-lie.net/nextcloud/index.php/s/MmXFYj6mGoMQoJN) for english
    * [here](https://the-cake-is-a-lie.net/nextcloud/index.php/s/HgqpQ6rFadtWSAt) for german

In [4]:
data_root_folder = "./data_en/" # i created a symlink here

* get all json files in `data_root_folder`

In [5]:
json_files = sorted(glob.glob(data_root_folder + "/*.json"))

----

* so far, only load the first file

In [6]:
twitter_data = pd.read_json(json_files[0], encoding="utf-8")
twitter_data

EMOJI  \
0                           [🔥, 👏]   
1                              [🤦]   
2                              [😄]   
3                              [📷]   
4                           [😩, 😩]   
5                           [😭, 💓]   
6                              [😂]   
7                              [💯]   
8                              [🙄]   
9                        [😟, 😥, 😢]   
10                             [🌻]   
11                       [🍁, 🌺, 🍂]   
12                             [🍃]   
13                          [💭, 🤦]   
14                          [😍, 😘]   
15                             [😜]   
16                          [😂, 🔥]   
17                             [💕]   
18                             [😉]   
19                             [👅]   
20                          [👌, 🙂]   
21                          [🤗, 📺]   
22                             [💯]   
23                       [👅, 💦, 🍑]   
24                             [💔]   
25                       [🤐, 🤐, 🤐]   
26                             [😴]   
27                             [😂]   
28                          [😂, 🙄]   
29              [🎉, 🎂, 🎈, 🎊, 🎁, 💜]   
...                            ...   
68703                          [😕]   
68704                       [😂, 😩]   
68705                          [😂]   
68706                          [💖]   
68707                 [🌆, 👉, 🚖, 📞]   
68708                          [😁]   
68709                          [😋]   
68710                    [👌, 🎃, 😘]   
68711                          [👍]   
68712                          [😭]   
68713                          [😂]   
68714                    [😭, 😭, 💘]   
68715                       [😫, ✋]   
68716                       [😂, 🙁]   
68717                          [😭]   
68718                       [😢, 💔]   
68719                          [🙃]   
68720              [😂, 😂, 😂, 😂, 😂]   
68721                    [👌, 👊, 🙌]   
68722                          [😴]   
68723                 [😂, 😂, 😂, 😂]   
68724                          [😀]   
68725                          [😎]   
68726                          [✨]   
68727                          [🤷]   
68728                          [😘]   
68729                          [😂]   
68730                          [🙏]   
68731                          [💁]   
68732  [🍃, 🌻, 🌻, 🍃, 🍃, 💐, 💐, 🍃, 🙋]   

                                              HASHTAGS  \
0                                                   []   
1                                                   []   
2                                                   []   
3                                                   []   
4                                                   []   
5                                                   []   
6                                                   []   
7                                                   []   
8                                                   []   
9                                                   []   
10                                                  []   
11                                                  []   
12         [#mortdale, #partofthefamily, #gorgeousboy]   
13                                                  []   
14                                     [#7YearsOfKMH2]   
15                                                  []   
16                                                  []   
17                                                  []   
18                                                  []   
19                                 [#footfetishnation]   
20                                                  []   
21                                                  []   
22                                                  []   
23                                                  []   
24                                                  []   
25                                                  []   
26                                                  []   
27                                              

* extracting emojis and text

In [7]:
emojis = twitter_data['EMOJI']
plain_text = twitter_data['text']

* make our plain text more "plain":
    * removing the keyword `<EMOJI>` (just for the beginning)
    * removing remaining useless emojis, like skin modifier etc.

In [8]:
# defining blacklist for modifier emojis:
emoji_blacklist = set([
    chr(0x1F3FB),
    chr(0x1F3FC),
    chr(0x1F3FD),
    chr(0x1F3FE),
    chr(0x1F3FF),
    chr(0x2642),
    chr(0x2640)
])

In [9]:
# filtering them and the EMOJI keyword out:
plain_text = plain_text.str.replace("(<EMOJI>|<USER>|<HASHTAG>)","").str.replace("[" + "".join(list(emoji_blacklist)) + "]","")

* convert all emojis to a sentiment vector

In [11]:
labels = emoji2sent([latest(e) for e in emojis])


In [12]:
len(labels)

68733

In [13]:
wrong_labels = np.isnan(np.linalg.norm(labels, axis=1))

* remove all data we have no label for

In [14]:
labels = labels[np.invert(wrong_labels)]
plain_text = plain_text[np.invert(wrong_labels)]
emojis = emojis[np.invert(wrong_labels)]

In [15]:
print(len(labels), len(emojis), len(plain_text))

33368 33368 33368


* Apply stemming and lemmatization (if needed)

In [16]:
from nltk.stem.snowball import SnowballStemmer
from nltk.stem import WordNetLemmatizer
from nltk import pos_tag
from nltk import word_tokenize
from nltk.corpus import wordnet

In [17]:
def get_wordnet_pos(treebank_tag):

    if treebank_tag.startswith('J'):
        return wordnet.ADJ
    elif treebank_tag.startswith('V'):
        return wordnet.VERB
    elif treebank_tag.startswith('N'):
        return wordnet.NOUN
    elif treebank_tag.startswith('R'):
        return wordnet.ADV
    else:
        return wordnet.NOUN

In [18]:
stemmer = SnowballStemmer("english")
for key in plain_text.keys():
    stemmed_sent = []
    for word in plain_text[key].split(" "):
        word_stemmed = stemmer.stem(word)
        stemmed_sent.append(word_stemmed)
    stemmed_sent = (" ").join(stemmed_sent)
    plain_text[key] = stemmed_sent

In [19]:
lemmatizer = WordNetLemmatizer()
for key in plain_text.keys():
    lemmatized_sent = []
    sent_pos = pos_tag(word_tokenize(plain_text[key]))
    for word in sent_pos:
        wordnet_pos = get_wordnet_pos(word[1].lower())
        word_lemmatized = lemmatizer.lemmatize(word[0], pos=wordnet_pos)
        lemmatized_sent.append(word_lemmatized)
    lemmatized_sent = (" ").join(lemmatized_sent)
    plain_text[key] = lemmatized_sent
print(plain_text)

2                                              woooaaaahhh
4                                        i wan na know too
6        i 'm le stress about turn 30 now i think i'v r...
9                                        got me emot there
14                                 cutest son roll no . 31
15       by the summer i should have everyth up and run...
18                 that pictur wa not taken this morning !
26       i so can not be bother with the rest of the da...
27                                                2lit4lif
35       hate fall asleep befor i put my phone on the c...
36       unexpect saw two of my crush today . this day ...
40       elvi whi o whi ? our girl wa such a love stori...
42                               you'r late i ate them all
43                                                me toooo
47                            the pressur is just too much
51                                         i broke grammar
52                      have not desir to go to work tod

* generate weights:

In [20]:
# at first count over our table
emoji_count = {}


for e_list in emojis:
    for e in set(e_list):
        if e not in emoji_count:
            emoji_count[e] = 0
        emoji_count[e] += 1

emoji_count
emoji_sum = sum([emoji_count[e] for e in emoji_count])

emoji_weights = {}
for e in emoji_count:
    # tfidf for emojis
    emoji_weights[e] = np.log((emoji_sum / emoji_count[e]))

weights_sum= sum([emoji_weights[x] for x in emoji_weights])
    
# normalize:
for e in emoji_weights:
    emoji_weights[e] = emoji_weights[e] / weights_sum

emoji_weights['X'] = 0  # dummy values
emoji_count['X'] = 0

* most used emojis in Dataset

In [21]:
import operator

In [22]:
sorted_emoji_count = list(reversed(sorted(emoji_count.items(), key=operator.itemgetter(1))))
display(sorted_emoji_count[:20])

top_emojis = [x[0] for x in sorted_emoji_count[:20]]
display(top_emojis)

[('😂', 10182),
 ('😭', 3893),
 ('😍', 2866),
 ('😩', 1647),
 ('😊', 1450),
 ('😘', 1151),
 ('🙏', 1089),
 ('🙌', 1003),
 ('😉', 752),
 ('😁', 697),
 ('😅', 651),
 ('😎', 606),
 ('😢', 544),
 ('😒', 539),
 ('😏', 478),
 ('😌', 434),
 ('😔', 415),
 ('😋', 397),
 ('😀', 392),
 ('😤', 368)]

['😂',
 '😭',
 '😍',
 '😩',
 '😊',
 '😘',
 '🙏',
 '🙌',
 '😉',
 '😁',
 '😅',
 '😎',
 '😢',
 '😒',
 '😏',
 '😌',
 '😔',
 '😋',
 '😀',
 '😤']

* only learn the most used ones:

In [23]:
in_top = [sentiment_vector_to_emoji(x) in top_emojis for x in labels]
labels = labels[in_top]
plain_text = plain_text[in_top]
emojis = emojis[in_top]
print(len(labels), len(emojis), len(plain_text))

26197 26197 26197


* generating train and test set:

In [24]:
X1, Xt1, y1, yt1 = train_test_split(plain_text, labels, test_size=0.1, random_state=4222)

In [25]:
#y1_weights = np.array([(sum([emoji_weights[e] for e in e_list]) / len(e_list)) if len(e_list) > 0 else 0 for e_list in sent2emoji(y1)])

In [26]:
vectorizer = TfidfVectorizer(stop_words='english')
vec_train = vectorizer.fit_transform(X1)
vec_test = vectorizer.transform(Xt1)

* train. this can take a very long time...

In [27]:
from sklearn.neural_network import MLPClassifier as MLP
from sklearn.multiclass import OneVsRestClassifier as OVRC
from sklearn.tree import DecisionTreeClassifier as DTC

from keras.models import Sequential
from keras.layers import Dense

Using TensorFlow backend.


In [28]:
def train(max_size = 10000, layers=[(1024, 'relu'),(y1[0].shape[0],'softmax')], random_state=4222, ovrc=False, n_iter=5):
    
    model = Sequential()
    
    # build mlp layers:
    keras_layers = []
    first_layer = True
    for layer in layers:
        if first_layer:
            model.add(Dense(units=layer[0], activation=layer[1], input_dim=vectorizer.transform([" "])[0]._shape[1]))
            first_layer = False
        else:
            model.add(Dense(units=layer[0], activation=layer[1]))
    
    #mlp = MLPClassifier(layers=sknn_layers, random_state=random_state, verbose=True, n_iter=n_iter, batch_size=100)
    
    model.compile(loss='mean_squared_error',
              optimizer='adam')
    
    clf = OVRC(model) if ovrc else model

    clf.fit(vec_train[:max_size].A, y1[:max_size], validation_split=0.2, epochs=n_iter)#, sample_weight=y1_weights[:max_size])
    
    return clf

In [29]:
clf = train(max_size=100000,layers=[(10000, 'relu'),(5000, 'relu'),(2500, 'relu'),(y1[0].shape[0],None)], n_iter=3)

Train on 18861 samples, validate on 4716 samples
Epoch 1/3
18861/18861 [==============================] - 1106s 59ms/step - loss: 0.0185 - val_loss: 0.0152
Epoch 2/3
18861/18861 [==============================] - 1104s 59ms/step - loss: 0.0107 - val_loss: 0.0163
Epoch 3/3
18861/18861 [==============================] - 1106s 59ms/step - loss: 0.0065 - val_loss: 0.0166


* make a prediction and store it in a csv file:

In [30]:
pred = clf.predict(vectorizer.transform(Xt1))

In [31]:
print(np.linalg.norm(np.var(pred, axis=0)))
print(np.linalg.norm(np.var(labels, axis=0)))


0.011668838
0.03387511671001757


In [32]:
# build a dataframe to visualize test results:
testlist = pd.DataFrame({'text': Xt1, 
                         'teacher': sent2emoji(yt1),
                         'teacher_sentiment': yt1.tolist(),
                         'predict': sent2emoji(pred, custom_target_emojis=top_emojis),
                         'predicted_sentiment': pred.tolist()})

In [33]:
display(testlist)


text teacher  \
35671    i feel like i care so much more in everi situat       😂   
25683  i did not meat to add that 2 there ... hav see...       😂   
8985                                              never…       😊   
5410            lmao on me ! ! ! wtf wa he suppos to say       😂   
62611  this dude alway help me get through my school ...       😊   
48197                                    happi b'day sir       😊   
23654       you need some good old fashion swedish jesus       🙏   
58207  these late shift are make me not have a social...       😅   
374                                      dc this weekend       😍   
26310                      paul lad you 'll make e blush       😊   
30892                     did you have a fun halloween ?       😂   
11868                                         hi handsom       😍   
46219         i 'm not okay with this , i 'm su snapchat       😭   
13583  my parent be so mad i be buy new stuff & amp ;...       😭   
43843  one of the few song that calm me down esp on f...       😂   
63589        iphon x bouta be the last phone we ever buy       😂   
53695            visit my main man today ❤ i miss u papa       😭   
67529                                              donut       😍   
25493  ha anyon heard this by ? who the fuck knew he ...       😘   
19486                                       wow superrbb       😍   
48449  of cours they do n't . their perfect model of ...       😂   
4504         plea pick me . pick me . pick me . please .       😍   
40285                             shiid no crack is wack       😭   
56741                      pj still sleep like a newborn       😩   
22948  an opinion doe n't mean you make sen first off...       😌   
68426                                        missyou too       😘   
13431                                    i swear she did       😩   
66287           it true , he wa the mutt ( big-d ) nut .       😉   
41980                                 is happen so happi       😭   
34632  saw that the first one said sose you tmmrw and np       😂   
...                                                  ...     ...   
47218                           keep it i do n't want it       😂   
35087  6 year ago today we said our final good bye , ...       😢   
61252                                               amen       🙏   
39960                                               fact       😎   
365                       nw final found someon hi loydi       😅   
50665                       i need ur shoulder to cri on       😢   
21007               awww you 'll get me teari eye gurl !       😘   
18819   〰happi hump day to all my ladi is def sweet like       😘   
42421                                           thanks .       😊   
38705  it okay i did n't see you until i wa in your face       😂   
47033                        fall in with alexissdang ⬅️       😍   
38742             let your wild side free girl ! ! ! ! !       😂   
67610                    can we get season 3 already ! ?       😭   
61021            have to quot this bih rememb this nigga       😂   
14904                                         he so damn       😩   
50994  yasss it time for a great show maxloyal™♛ : gi...       😂   
6973                     got to love a fish finger sarni       😂   
3269                                             say dat       😂   
54827                             if ur happi i 'm happi       😊   
19409                                           rockstar       😀   
38703                   god fuck me i alreadi fix it onc       😂   
25133  it social accept to listen to ani christma mus...       😂   
15339      i thrash p in imessag now he wan na bet on 2k       😂   
28082  my fatass need some lemon pepper wing w a lil ...       😂   
44462  fck off tristan yes soph collect u in 15 n we ...       😤   
60212                                       open the bag       😋   
34950  i ask peopl to guess my zodiac sign and this o...       😤   
59462                                   

* exactly correct labeled sentences:

In [34]:
print (sum([1 if sample[1]['teacher'] == sample[1]['predict'] else 0 for sample in testlist.iterrows()]) / testlist.shape[0])

0.1851145038167939


* mean squared error:

In [35]:
teacher_sentiments = np.array([sample[1]['teacher_sentiment'] for sample in testlist.iterrows()])
predicted_sentiments = np.array([sample[1]['predicted_sentiment'] for sample in testlist.iterrows()])

mean_squared_error = ((teacher_sentiments - predicted_sentiments)**2).mean(axis=0)
display(mean_squared_error)

array([0.02218282, 0.02594105, 0.00323429])

* by an overall variance of:

In [36]:
print("Variance teacher: ", np.var(teacher_sentiments, axis=0))
print("Variance prediction: ", np.var(predicted_sentiments, axis=0))

Variance teacher:  [0.02183094 0.02513847 0.00285735]
Variance prediction:  [0.00850173 0.00793481 0.00095984]


In [37]:
testlist.to_csv('test.csv')

* save classifier:

In [38]:
import pickle
clf.save("clf2.keras")
pickle.dump( vectorizer, open( "vec2.pickle", "wb" ) )

----
## testing area

**for just testing, start from here!**

download the dumped classifier and vectorizer from [here](https://the-cake-is-a-lie.net/nextcloud/index.php/s/NjMXamfwQsyrefG)

* loading classifier and vectorizer

In [14]:
from IPython.display import clear_output, Markdown, Math
import ipywidgets as widgets
import sys
sys.path.append("..")

from Tools.Emoji_Distance import sentiment_vector_to_emoji
from Tools.Emoji_Distance import emoji_to_sentiment_vector

def emoji2sent(emoji_arr):
    return np.array([emoji_to_sentiment_vector(e) for e in emoji_arr])

def sent2emoji(sent_arr, custom_target_emojis=None):
    return [sentiment_vector_to_emoji(s, custom_target_emojis=custom_target_emojis) for s in sent_arr]

In [ ]:
import keras
import pickle
clf = keras.models.load_model("clf.keras")
vectorizer = pickle.load( open( "vec.pickle", "rb" ) )

* define lookup emojis here:

In [6]:
lookup_emojis = [#'😂',
 '😭',
 '😍',
 '😩',
 '😊',
 '😘',
 '🙏',
 '🙌',
 '😉',
 '😁',
 '😅',
 '😎',
 '😢',
 '😒',
 '😏',
 '😌',
 '😔',
 '😋',
 '😀',
 '😤']

* a simple output widget for testing:

In [19]:
out = widgets.Output()

t = widgets.Text()
b = widgets.Button(
    description='get emoji',
    disabled=False,
    button_style='', # 'success', 'info', 'warning', 'danger' or ''
    tooltip='Click me',
    icon='check'
)



def handle_submit(sender):
    with out:
        clear_output()
    with out:
        pred = clf.predict(vectorizer.transform([t.value]))
        
        display(Markdown("# Predicted Emoji " + str(sent2emoji(pred, lookup_emojis)[0])))
        display(Markdown("# Sentiment Vector: $$ \pmatrix{" + str(pred[0,0]) +
                         "\\\\" + str(pred[0,1]) + "\\\\" + str(pred[0,2]) + "}$$"))

b.on_click(handle_submit)
    
display(t)
display(widgets.VBox([b, out]))  

Text(value='')

In [5]:
import numpy as np

y_trans = mlb.inverse_transform(yt1)
pred_trans = mlb.inverse_transform(yt1)

# evaluate accuracy
pos = 0
neg = 0
all = 0
for entry in range(len(y_trans)):
    if len(np.intersect1d(y_trans[entry], pred_trans[entry])) > 0:
        pos += 1
    else:
        neg += 1
    all += 1
print(pos/all)
print(neg)

NameError: name 'mlb' is not defined